# String Manipulation

In [2]:
mssparkutils.notebook.run('4 - MSSpark Utilities/6 - Mount configuration')

StatementMeta(SmallSpark, 39, 3, Finished, Available)

'[MountPointInfo(mountPoint=/lake, source=abfss://refined@projectsynapsestorage.dfs.core.windows.net/, linkedService=storage, scope=job)]'

In [3]:
## - Accessing the Files from Mountpoint 
## Syntax:
# synfs:/<jobid>/<mountpoint>/<path>
# To get JobID - mssparkutils.env.getJobId()


job_id = mssparkutils.env.getJobId()

mount_point = 'synfs:/' + job_id + '/lake'

StatementMeta(SmallSpark, 39, 4, Finished, Available)

In [18]:
## Read the dataframe

df = spark.read.format('parquet')\
                .load(mount_point+'/JoinedData/*.parquet')

StatementMeta(SmallSpark, 39, 19, Finished, Available)

In [19]:
display(df)

StatementMeta(SmallSpark, 39, 20, Finished, Available)

SynapseWidget(Synapse.DataFrame, ee882247-bf08-4313-9be4-6834d6f2aeb3)

# Replace

In [20]:
# Getting all column names

AllColumns = df.columns

StatementMeta(SmallSpark, 39, 21, Finished, Available)

In [21]:
print(AllColumns)

StatementMeta(SmallSpark, 39, 22, Finished, Available)

['Education Level', 'Line_Number', 'Year', 'Month', 'State', 'Labor Force', 'Employed', 'Unemployed', 'Industry', 'Gender', 'Date Inserted', 'Aggregation Level', 'Data Accuracy', 'UnEmployed Rate Percentage', 'Expected Salary Range in USD']


In [22]:
# Using withColumnRenamed and replace function 

for column in AllColumns:
    df = df.withColumnRenamed(column,column.replace(' ','_'))

StatementMeta(SmallSpark, 39, 23, Finished, Available)

In [23]:
display(df)

StatementMeta(SmallSpark, 39, 24, Finished, Available)

SynapseWidget(Synapse.DataFrame, 9aa4949b-9aed-4a01-8f30-26618541fdf4)

# Split function

In [24]:
df.select('Expected_Salary_Range_in_USD').show()

StatementMeta(SmallSpark, 39, 25, Finished, Available)

+----------------------------+
|Expected_Salary_Range_in_USD|
+----------------------------+
|             100000 - 150000|
|               50000 - 70000|
|               60000 - 90000|
|              80000 - 120000|
|              70000 - 100000|
|              80000 - 120000|
|               50000 - 70000|
|              80000 - 120000|
|              80000 - 120000|
|              80000 - 120000|
|               60000 - 90000|
|             100000 - 150000|
|             100000 - 150000|
|             100000 - 150000|
|              80000 - 120000|
|             100000 - 150000|
|              80000 - 120000|
|              80000 - 120000|
|              80000 - 120000|
|               50000 - 70000|
+----------------------------+
only showing top 20 rows



In [30]:
from pyspark.sql.functions import *

df_split1 = df.withColumn("Min_Salary_USD",split("Expected_Salary_Range_in_USD"," - ")[0].cast('integer'))

StatementMeta(SmallSpark, 39, 31, Finished, Available)

In [31]:
display(df_split1)

StatementMeta(SmallSpark, 39, 32, Finished, Available)

SynapseWidget(Synapse.DataFrame, dac103d1-f6dd-496c-9e80-cca7ddf74118)

In [32]:
from pyspark.sql.functions import *

df_split2 = df_split1.withColumn("Max_Salary_USD",split("Expected_Salary_Range_in_USD"," - ")[1].cast('integer'))

StatementMeta(SmallSpark, 39, 33, Finished, Available)

In [33]:
display(df_split2)

StatementMeta(SmallSpark, 39, 34, Finished, Available)

SynapseWidget(Synapse.DataFrame, ab1726d5-e5b3-40fc-9f11-7f17c51d6eb9)

In [34]:
df_dropped = df_split2.drop('Expected_Salary_Range_in_USD')

StatementMeta(SmallSpark, 39, 35, Finished, Available)

In [35]:
display(df_dropped)

StatementMeta(SmallSpark, 39, 36, Finished, Available)

SynapseWidget(Synapse.DataFrame, cb71d13f-8795-432c-b202-2646d39288f3)

# Concat function

In [38]:
# Concat function 

from pyspark.sql.functions import col

display(df_dropped.withColumn("Month-Year",concat(col('Month'),lit('-'),col('Year'))))

StatementMeta(SmallSpark, 39, 39, Finished, Available)

SynapseWidget(Synapse.DataFrame, ed06976a-4dc9-4617-86ad-a3fd0bda0a63)

# Sorting and ordering

In [39]:
# 1- Orderby

df_dropped.orderBy('Date_Inserted').show()

StatementMeta(SmallSpark, 39, 40, Finished, Available)

+-------------------+-----------+----+-------+-----+-----------+--------+----------+------------------+------+-------------+-----------------+-------------+--------------------------+--------------+--------------+
|    Education_Level|Line_Number|Year|  Month|State|Labor_Force|Employed|Unemployed|          Industry|Gender|Date_Inserted|Aggregation_Level|Data_Accuracy|UnEmployed_Rate_Percentage|Min_Salary_USD|Max_Salary_USD|
+-------------------+-----------+----+-------+-----+-----------+--------+----------+------------------+------+-------------+-----------------+-------------+--------------------------+--------------+--------------+
|  Bachelor's Degree|        114|1995|    Jan|   CA|     130000|  117000|     13000|            Retail|  Male|     1/1/1995|          Country|Highly Random|                      10.0|         80000|        120000|
|  Bachelor's Degree|       1313|1995|January|   FL|    3000000| 2800000|    200000|     Manufacturing|  Male|     1/1/1995|          Country|Hi

In [41]:
df_dropped.orderBy(col('Date_Inserted').desc()).show()

StatementMeta(SmallSpark, 39, 42, Finished, Available)

+-------------------+-----------+----+---------+-----+-----------+--------+----------+-------------+------+-------------+-----------------+-------------+--------------------------+--------------+--------------+
|    Education_Level|Line_Number|Year|    Month|State|Labor_Force|Employed|Unemployed|     Industry|Gender|Date_Inserted|Aggregation_Level|Data_Accuracy|UnEmployed_Rate_Percentage|Min_Salary_USD|Max_Salary_USD|
+-------------------+-----------+----+---------+-----+-----------+--------+----------+-------------+------+-------------+-----------------+-------------+--------------------------+--------------+--------------+
|High School Diploma|         81|2022|      Sep|   NY|     105000|   94500|     10500|   Healthcare|Female|     9/1/2022|          Country|Highly Random|                      10.0|         50000|         70000|
|  Bachelor's Degree|         80|2022|      Sep|   NY|     200000|  180000|     20000|       Energy|  Male|     9/1/2022|          Country|Highly Random|   

In [42]:
# Identify what is the latest date inserted along with Highest Unemployment Rate 

display(df_dropped.orderBy(col('Date_Inserted').desc(),col('UnEmployed_Rate_Percentage').desc()))

StatementMeta(SmallSpark, 39, 43, Finished, Available)

SynapseWidget(Synapse.DataFrame, 18d74328-104c-4eea-995b-c13e6427a909)

In [44]:
df_ordered = df_dropped.orderBy(desc('Date_Inserted'), desc('UnEmployed_Rate_Percentage'))

StatementMeta(SmallSpark, 39, 45, Finished, Available)

## Sort()

In [45]:
df_dropped.sort(col('Date_Inserted')).show()

StatementMeta(SmallSpark, 39, 46, Finished, Available)

+-------------------+-----------+----+-------+-----+-----------+--------+----------+------------------+------+-------------+-----------------+-------------+--------------------------+--------------+--------------+
|    Education_Level|Line_Number|Year|  Month|State|Labor_Force|Employed|Unemployed|          Industry|Gender|Date_Inserted|Aggregation_Level|Data_Accuracy|UnEmployed_Rate_Percentage|Min_Salary_USD|Max_Salary_USD|
+-------------------+-----------+----+-------+-----+-----------+--------+----------+------------------+------+-------------+-----------------+-------------+--------------------------+--------------+--------------+
|  Bachelor's Degree|        114|1995|    Jan|   CA|     130000|  117000|     13000|            Retail|  Male|     1/1/1995|          Country|Highly Random|                      10.0|         80000|        120000|
|  Bachelor's Degree|       1313|1995|January|   FL|    3000000| 2800000|    200000|     Manufacturing|  Male|     1/1/1995|          Country|Hi

In [46]:
df_ordered.write.format('parquet')\
                .mode('overwrite')\
                .save(mount_point+'/StringSorted/')

StatementMeta(SmallSpark, 39, 47, Finished, Available)